In [ ]:
# import PyRosetta library
from pyrosetta import *
init()

In [ ]:
# clean and load a locally stored PDB
from pyrosetta.toolbox import cleanATOM
cleanATOM("/home/dimaio/Downloads/1ubq.pdb")
pose = pose_from_pdb("/home/dimaio/Downloads/1ubq.clean.pdb")

In [ ]:
# download a PDB from RCSB
from pyrosetta.toolbox import pose_from_rcsb
pose = pose_from_rcsb("1ubq")

In [ ]:
# querying the pose object
#print (pose.sequence())
#print ("Protein has", pose.total_residue(), "residues.")
#print (pose.residue(12))

In [ ]:
# querying pose geometry
for i in range(1,5):
    print ("phi",i,"=",pose.phi(i))
    print ("psi",i,"=",pose.psi(i))
    print ("omega",i,"=",pose.omega(i))

In [ ]:
dir(pose)

In [ ]:
import numpy
CA = pose.residue(12).atom("CA").xyz()
CA = numpy.array(CA)
CA

In [ ]:
%matplotlib widget
import numpy
import matplotlib.pyplot as plt
CAs = numpy.array([pose.residue(i).atom("CA").xyz() for i in range(1,pose.total_residue()+1)])
ax = plt.axes(projection='3d')
ax.plot3D(CAs[:,0], CAs[:,1], CAs[:,2])
plt.show()

In [ ]:
# query length/angle/dihedral
CA = pose.residue(3).atom("CA").xyz()
N = pose.residue(3).atom("N").xyz()
CA_N = (CA-N).length()
print ("CA:N dist",CA_N)

C = pose.residue(3).atom("C").xyz()
C_CA_N = pyrosetta.rosetta.numeric.angle_degrees(C,CA,N)
print ("C:CA:N angle",C_CA_N)

Np1 = pose.residue(4).atom("N").xyz()
NCACNp = pyrosetta.rosetta.numeric.dihedral_degrees(N,CA,C,Np1)
print ("N:CA:C:N(+1) dihedral",NCACNp)

In [ ]:
# print the atom names in a residue
for i in range(1,pose.residue_type(2).natoms()+1):
    print (i,pose.residue_type(2).atom_name(i))

In [ ]:
# query bond connectivity
CA_index = (pose.residue_type(2).atom_index("CA"))
nbrs = pose.residue_type(2).nbrs(CA_index)
print ("Neighbors:")
for i in nbrs:
    print (pose.residue_type(2).atom_name(i))

In [ ]:
# set geometry
pose = pose_from_rcsb("1ubq")
pose.set_phi(5, -60)
pose.set_psi(5, -43)
pose.set_chi(1, 5, 180)

# write PDB to disk
pose.dump_pdb("/home/dimaio/Downloads/1ubq_modified.pdb")

In [ ]:
# score a pose with the default energy function
pose = pose_from_rcsb("1ubq")
scorefxn = get_fa_scorefxn()
#scorefxn(pose)
scorefxn.show(pose)

In [ ]:
# score a pose with a custom scorefunction
scorefxn = ScoreFunction()
scorefxn.set_weight(rosetta.core.scoring.fa_atr, 1.0)
scorefxn.set_weight(rosetta.core.scoring.fa_rep, 1.0)
scorefxn.set_weight(rosetta.core.scoring.fa_elec, 1.0)

scorefxn.show(pose)

# show the energy of a single residue
pose.energies().show(12)

In [ ]:
## generate a model with a given sequence
pose = pose_from_sequence("AKA")
pose.set_phi(1,-120)
pose.set_psi(1,120)
pose.set_phi(2,-60)
pose.set_psi(2,-50)
pose.set_phi(3,-120)
pose.set_psi(3,120)
pose.dump_pdb("/home/dimaio/Downloads/AKA.pdb")

In [ ]:
# integration with matplotlib...
# plot the phi/psis in 1oel
import numpy
import matplotlib.pyplot as plt
from pyrosetta.toolbox import pose_from_rcsb

# read the pose, allocate space for storage
pose = pose_from_rcsb("1ubq")
nres = pose.total_residue()
phipsis = numpy.zeros((2,nres-2))

for i in range(2,nres):
    phipsis[0,i-2] = pose.phi(i)
    phipsis[1,i-2] = pose.psi(i)

fig, ax = plt.subplots()
ax.scatter(phipsis[0,:],phipsis[1,:])
ax.set_xlim([-180,180])
ax.set_ylim([-180,180])
ax.set_aspect(1)

In [ ]:
# pack (optimize the sidechains of) a pose
scorefxn = get_fa_scorefxn()

pose = pose_from_rcsb("1ubq")

# build packer task
task_pack = standard_packer_task(pose)
task_pack.restrict_to_repacking()

print ("score before packing",scorefxn(pose))

pack_mover = (
   rosetta.protocols.minimization_packing.PackRotamersMover(
     scorefxn, task_pack))
pack_mover.apply(pose)

print ("score after packing",scorefxn(pose))
pose.dump_pdb("/home/dimaio/Downloads/1ubq_repacked.pdb")

In [ ]:
scorefxn.show(pose)

In [ ]:
# pack/design a single residue
scorefxn = get_fa_scorefxn()

#set initial pose
pose = pose_from_sequence("AKA")
pose.set_phi(1,-120)
pose.set_psi(1,120)
pose.set_phi(2,-60)
pose.set_psi(2,-50)
pose.set_phi(3,-120)
pose.set_psi(3,120)

#setup packer task
task_pack = standard_packer_task(pose)
task_pack.restrict_to_repacking()
task_pack.temporarily_fix_everything()
task_pack.temporarily_set_pack_residue(2, True)
pack_mover = (
   rosetta.protocols.minimization_packing.PackRotamersMover(
     scorefxn, task_pack))

#do the packing
pack_mover.apply(pose)
pose.dump_pdb("/home/dimaio/Downloads/AKA_res2.pdb")